In [1]:
# !pip3 install -U openai-whisper -i https://mirrors.aliyun.com/pypi/simple/
# !pip3 install jiwer -i https://mirrors.aliyun.com/pypi/simple/
# !pip3 install noisereduce -i https://mirrors.aliyun.com/pypi/simple/ 

In [1]:
import warnings
warnings.filterwarnings("ignore")

from pathlib import Path
from tqdm import tqdm
import torch
import librosa
import numpy as np
import glob
import os

import sys
sys.path.append("/home/shoinoue/Git/cuhksz-phd/sho_util/pyfiles/")
from sound import play_audio

import whisper
from whisper.normalizers.english import EnglishTextNormalizer
normalizer = EnglishTextNormalizer()
import jiwer
import pandas as pd
import scipy.stats as st
import math
from IPython.display import clear_output

sr = 16000

## Whisper

In [2]:
models = {
    # "tiny": whisper.load_model("tiny.en"),
    # "base": whisper.load_model("base.en"),
    # "small": whisper.load_model("small.en"),
    # "medium": whisper.load_model("medium.en"),
    "large": whisper.load_model("large"),
}

In [3]:
files = glob.glob("./SPAT/transliteration/*.npy")
files.sort()
groundtruth_dir = {}
for file in files:
    key = os.path.basename(file)[:-4]
    text = np.load(file, allow_pickle=True).item()["Original English"]
    groundtruth_dir[key] = normalizer(text)

In [4]:
base_model_dir = "/mntcephfs/lab_data/shoinoue/Models/trained_models/AC_01/ckpts_16000/"
model_paths = [
    # "VTN_fine-tuning_nocondition_gt2syn_melmel_hubert_norepeating_smaller/100000",
    # "VTN_fine-tuning_nocondition_gt2syn_melmel_hubert_norepeating_small/100000",
    # "VTN_fine-tuning_nocondition_gt2syn_melmel_hubert_norepeating/100000",
    # "VTN_fine-tuning_nocondition_mix2synVCTK3hr_melmel_hubert_norepeating_smaller/100000",
    # "VTN_fine-tuning_nocondition_mix2synVCTK3hr_melmel_hubert_norepeating_small/100000",
    # "VTN_fine-tuning_nocondition_mix2synVCTK3hr_melmel_hubert_norepeating/100000",
    
    # "VTN_fine-tuning_nocondition_gt2syn_80mel80mel_hubert_norepeating_small/100000",
    # "VTN_fine-tuning_nocondition_gt2syn_80mel80mel_hubert_norepeating/100000",
    # "VTN_fine-tuning_nocondition_mix2synVCTK3hr_80mel80mel_hubert_norepeating_small/100000",
    # "VTN_fine-tuning_nocondition_mix2synVCTK3hr_80mel80mel_hubert_norepeating/100000",
    
    # "VTN_fine-tuning_nocondition_gt2syn_hifiganmelhifiganmel_hubert_norepeating/100000",
    "VTN_fine-tuning_nocondition_mix2synVCTK3hr_hifiganmelhifiganmel_hubert_norepeating/100000",
]
base_dataset_dir = "/mntcephfs/lab_data/shoinoue/Dataset/"
dataset_paths = [
    # "PD-AST/SLT/English",
    # "PD-AST/SLT/Hindi",
    # "PD-AST/SLT/Korean",
    # "PD-AST/ASI/Hindi",
    # "PD-AST/TNI/Hindi",
    # "PD-AST/HKK/Korean",
    # "PD-AST/YDCK/Korean",
    # "CMU-ARCTIC/SLT",
    # "L2-ARCTIC/ASI",
    # "L2-ARCTIC/TNI",
    # "L2-ARCTIC/HKK",
    # "L2-ARCTIC/YDCK",
]

In [12]:
save_dir = f"evaluation/wers/individual/"
testsamples = list(np.load("data_split_ARCTIC.npy", allow_pickle=True))[2]
for ij in range(2):
    base_dir = [base_model_dir, base_dataset_dir][ij]
    dirnames = [model_paths, dataset_paths][ij]
    for dirname in dirnames:
        save_path = save_dir + f'{"___".join(dirname.split("/"))}.npy'
        # if os.path.exists(save_path):
        #     continue
        print(dirname)
        files = glob.glob(base_dir + f"{dirname}/wav/*.wav")
        files.sort()
        wers = []
        cers = []
        for size in models:
            predtexts = []
            gttexts = []
            for path in tqdm(files):
                basename = os.path.basename(path)[:-4]
                if not(basename in testsamples):
                    continue
                predtext = normalizer(models[size].transcribe(path)["text"])
                predtexts += [predtext]
                gttexts += [groundtruth_dir[basename]]
                # if len(gttexts)>5:
                #     break
            wer = jiwer.wer(gttexts, predtexts)
            cer = jiwer.cer(gttexts, predtexts)
            wers += [wer]
            cers += [cer]
        # np.save(save_path, [wers, cers])

VTN_fine-tuning_nocondition_mix2synVCTK3hr_hifiganmelhifiganmel_hubert_norepeating/100000


100%|██████████| 100/100 [01:15<00:00,  1.33it/s]


In [17]:
wer_list = []
for i in range(len(gttexts)):
    wer = jiwer.wer([gttexts[i]], [predtexts[i]])
    wer_list += [wer]
wer_list = np.array(wer_list)

In [31]:
werbool = wer_list==0
accentbool = np.array([ True,  True,  True,  True,  True,  True,  True,  True, False,
                       True,  True, False,  True,  True,  True, False,  True,  True,
                       True,  True, False,  True,  True, False,  True,  True,  True,
                       False,  True,  True,  True,  True,  True,  True,  True, False,
                       True,  True,  True,  True,  True,  True,  True,  True,  True,
                       True,  True,  True,  True,  True,  True,  True,  True,  True,
                       True,  True,  True, False,  True, False,  True,  True,  True,
                       True, False,  True, False,  True,  True,  True,  True, False,
                       True,  True,  True,  True,  True, False, False,  True,  True,
                       True,  True,  True,  True,  True,  True,  True,  True,  True,
                       True,  True,  True,  True,  True,  True,  True,  True,  True,
                       False])

In [32]:
werbool

array([ True,  True,  True,  True,  True, False,  True,  True,  True,
       False, False, False,  True,  True,  True, False,  True, False,
        True,  True,  True,  True,  True, False, False,  True, False,
        True,  True, False,  True,  True,  True, False,  True, False,
       False, False,  True, False, False,  True,  True,  True,  True,
       False,  True, False, False, False,  True,  True, False,  True,
        True,  True, False, False,  True,  True, False,  True,  True,
        True,  True, False,  True, False, False,  True, False, False,
        True,  True, False,  True,  True, False,  True, False,  True,
       False,  True,  True, False,  True, False,  True,  True,  True,
       False, False,  True,  True, False,  True, False, False,  True,
        True])

In [36]:
bl = werbool*accentbool
bl.sum()

52

In [39]:
list(np.array([os.path.basename(a)[:-4] for a in files])[bl])

['arctic_a0024',
 'arctic_a0029',
 'arctic_a0058',
 'arctic_a0073',
 'arctic_a0085',
 'arctic_a0092',
 'arctic_a0099',
 'arctic_a0131',
 'arctic_a0152',
 'arctic_a0170',
 'arctic_a0202',
 'arctic_a0210',
 'arctic_a0245',
 'arctic_a0258',
 'arctic_a0274',
 'arctic_a0315',
 'arctic_a0369',
 'arctic_a0374',
 'arctic_a0378',
 'arctic_a0384',
 'arctic_a0389',
 'arctic_a0449',
 'arctic_a0544',
 'arctic_a0545',
 'arctic_a0552',
 'arctic_a0556',
 'arctic_a0561',
 'arctic_b0008',
 'arctic_b0019',
 'arctic_b0047',
 'arctic_b0067',
 'arctic_b0083',
 'arctic_b0113',
 'arctic_b0142',
 'arctic_b0147',
 'arctic_b0163',
 'arctic_b0190',
 'arctic_b0210',
 'arctic_b0224',
 'arctic_b0253',
 'arctic_b0257',
 'arctic_b0296',
 'arctic_b0317',
 'arctic_b0318',
 'arctic_b0339',
 'arctic_b0372',
 'arctic_b0380',
 'arctic_b0381',
 'arctic_b0469',
 'arctic_b0474',
 'arctic_b0497',
 'arctic_b0508']

# Analysis

In [4]:
def get_basic_info(key):
    key1 = key.split("/")[0]
    if "ARCTIC" in key1:
        data_type = "Ground Truth"
        speaker = key.split("/")[1]
        accent = spk2acc[speaker]
    elif "PD-AST"==key1:
        data_type = "SPAccenT"
        speaker, accent = key.split("/")[1:]
    else:
        data_type = "AC_"
        if "smaller" in key1:
            data_type += "small"
        elif "small" in key1:
            data_type += "normal"
        else:
            data_type += "large"
        if "VCTK" in key1:
            data_type += "_VCTK"
        speaker = "SLT"
        accent = mode
    return data_type, speaker, accent

new_columns = []
for cl in ["Data Type", "Speaker", "Accent"]:
    new_columns += [("basics", cl)]
for cl in models:
    new_columns += [("scores", cl)]
new_columns = pd.MultiIndex.from_tuples(new_columns)

spk2acc = {
    "SLT": "English",
    "ASI": "Hindi",
    "TNI": "Hindi",
    "HKK": "Korean",
    "YDCK": "Korean",
}

NameError: name 'models' is not defined

In [15]:
mode = "Hindi"
if mode=="Hindi":
    labels = [
        "CMU-ARCTIC/SLT",
        "L2-ARCTIC/ASI",
        "L2-ARCTIC/TNI",
        "PD-AST/SLT/English",
        "PD-AST/SLT/Hindi",
        "PD-AST/ASI/Hindi",
        "PD-AST/TNI/Hindi",
        "VTN_fine-tuning_nocondition_gt2syn_melmel_hubert_norepeating_smaller/100000",
        "VTN_fine-tuning_nocondition_gt2syn_melmel_hubert_norepeating_small/100000",
        "VTN_fine-tuning_nocondition_gt2syn_melmel_hubert_norepeating/100000",
        "VTN_fine-tuning_nocondition_mix2synVCTK3hr_melmel_hubert_norepeating_smaller/100000",
        "VTN_fine-tuning_nocondition_mix2synVCTK3hr_melmel_hubert_norepeating_small/100000",
        "VTN_fine-tuning_nocondition_mix2synVCTK3hr_melmel_hubert_norepeating/100000",
    ]
elif mode=="Korean":
    labels = [
        "L2-ARCTIC/HKK",
        "L2-ARCTIC/YDCK",
        "PD-AST/SLT/English",
        "PD-AST/SLT/Korean",
        "PD-AST/HKK/Korean",
        "PD-AST/YDCK/Korean",
    ]

In [16]:
save_dir = f"evaluation/wers/individual/"
basics = []
wers = []
cers = []
for dirname in labels:
    data_type, speaker, accent = get_basic_info(dirname)
    path = save_dir + f'{"___".join(dirname.split("/"))}.npy'
    wer_list, cer_list = np.load(path)
    wers += [list(wer_list)]
    cers += [list(cer_list)]
    basics += [[data_type, speaker, accent]]
    
array = np.concatenate([basics, wers], axis=1)
df = pd.DataFrame(array, columns=new_columns)
df.loc[:, "scores"] =  df.loc[:, "scores"].values.astype(float)
df

basics                     scores                                \
         Data Type Speaker   Accent      tiny      base     small    medium   
0     Ground Truth     SLT  English  0.059016  0.033880  0.025137  0.025137   
1     Ground Truth     ASI    Hindi  0.145355  0.093989  0.067760  0.062295   
2     Ground Truth     TNI    Hindi  0.191257  0.125683  0.077596  0.067760   
3         SPAccenT     SLT  English  0.036066  0.026230  0.021858  0.028415   
4         SPAccenT     SLT    Hindi  0.203279  0.149727  0.113661  0.110383   
5         SPAccenT     ASI    Hindi  0.158470  0.123497  0.092896  0.090710   
6         SPAccenT     TNI    Hindi  0.157377  0.104918  0.085246  0.084153   
7         AC_small     SLT    Hindi  0.712568  0.532240  0.446995  0.413115   
8        AC_normal     SLT    Hindi  0.361749  0.316940  0.246995  0.215301   
9         AC_large     SLT    Hindi  0.355191  0.349727  0.285246  0.265574   
10   AC_small_VCTK     SLT    Hindi  0.471038  0.414208  0.336612  0.299454   
11  AC_normal_VCTK     SLT    Hindi  0.314754  0.274317  0.221858  0.185792   
12   AC_large_VCTK     SLT    Hindi  0.237158  0.215301  0.172678  0.148634   

              
       large  
0   0.019672  
1   0.046995  
2   0.057923  
3   0.017486  
4   0.085246  
5   0.093989  
6   0.076503  
7   0.381421  
8   0.177049  
9   0.212022  
10  0.242623  
11  0.165027  
12  0.106011

# Listen to Samples

In [24]:
base_model_dir = "/mntcephfs/lab_data/shoinoue/Models/trained_models/AC_01/ckpts_16000/"
model_paths = [
    # "VTN_fine-tuning_nocondition_gt2syn_melmel_hubert_norepeating_smaller/100000",
    # "VTN_fine-tuning_nocondition_gt2syn_melmel_hubert_norepeating_small/100000",
    # "VTN_fine-tuning_nocondition_gt2syn_melmel_hubert_norepeating/100000",
    "VTN_fine-tuning_nocondition_mix2synVCTK3hr_melmel_hubert_norepeating_small/100000",
    "VTN_fine-tuning_nocondition_mix2synVCTK3hr_melmel_hubert_norepeating/100000",
    
    # "VTN_fine-tuning_nocondition_gt2syn_80mel80mel_hubert_norepeating_small/100000",
    # "VTN_fine-tuning_nocondition_gt2syn_80mel80mel_hubert_norepeating/100000",
    "VTN_fine-tuning_nocondition_mix2synVCTK3hr_80mel80mel_hubert_norepeating_small/100000",
    "VTN_fine-tuning_nocondition_mix2synVCTK3hr_80mel80mel_hubert_norepeating/100000",
]
base_dataset_dir = "/mntcephfs/lab_data/shoinoue/Dataset/"
dataset_paths = [
    "CMU-ARCTIC/SLT",
    "PD-AST/SLT/English",
    "PD-AST/SLT/Hindi",
    # "PD-AST/SLT/Korean",
    # "PD-AST/ASI/Hindi",
    # "PD-AST/TNI/Hindi",
    # "PD-AST/HKK/Korean",
    # "PD-AST/YDCK/Korean",
    # "L2-ARCTIC/ASI",
    # "L2-ARCTIC/TNI",
    # "L2-ARCTIC/HKK",
    # "L2-ARCTIC/YDCK",
]
testsamples = list(np.load("data_split_ARCTIC.npy", allow_pickle=True))[2]

In [28]:
start = 15
num = 10
for basename in testsamples[start:start+num]:
    for ij in range(2):
        base_dir = [base_model_dir, base_dataset_dir][1-ij]
        dirnames = [model_paths, dataset_paths][1-ij]
        for dirname in dirnames:
            print(dirname)
            path = base_dir + dirname + f"/wav/{basename}.wav"
            x, sr = librosa.load(path, sr=16000)
            play_audio(x, sr)
    print("----------------------")

CMU-ARCTIC/SLT


PD-AST/SLT/English


PD-AST/SLT/Hindi


VTN_fine-tuning_nocondition_mix2synVCTK3hr_melmel_hubert_norepeating_small/100000


VTN_fine-tuning_nocondition_mix2synVCTK3hr_melmel_hubert_norepeating/100000


...

VTN_fine-tuning_nocondition_mix2synVCTK3hr_melmel_hubert_norepeating_small/100000


VTN_fine-tuning_nocondition_mix2synVCTK3hr_melmel_hubert_norepeating/100000


VTN_fine-tuning_nocondition_mix2synVCTK3hr_80mel80mel_hubert_norepeating_small/100000


VTN_fine-tuning_nocondition_mix2synVCTK3hr_80mel80mel_hubert_norepeating/100000


----------------------
